In [1]:
from keras.models import Sequential
from keras import layers
import numpy as np
from six.moves import range

Using TensorFlow backend.


# Parameters Config

In [2]:
class colors:
    ok='\033[92m'
    fail='\033[91m'
    close='\033[0m'

In [3]:
TRAINING_SIZE=80000
DIGITS=3
REVERSE=False
MAXLEN=DIGITS+1+DIGITS+1+DIGITS
chars='0123456789+ '
RNN=layers.LSTM
HIDDEN_SIZE=128
BATCH_SIZE=128
LAYERS=1

In [4]:
class CharacterTable(object):
    def __init__(self,chars):
        self.chars=sorted(set(chars))
        self.char_indices=dict((c,i) for i,c in enumerate(self.chars))
        self.indices_char=dict((i,c) for i,c in enumerate(self.chars))
    
    def encode(self,C,num_rows): #input C is string
        x=np.zeros((num_rows, len(self.chars)))
        for i,c in enumerate(C):
            x[i,self.char_indices[c]]=1
        return x
    
    def decode(self,x,calc_argmax=True): #if input x is 1-D array then culc_argmax=True； otherwise, if x is string or int then False
        if calc_argmax:
            x=x.argmax(axis=-1)
        return "".join(self.indices_char[i] for i in x)
    

In [5]:
ctable=CharacterTable(chars)

In [6]:
print(ctable.indices_char)
print(ctable.char_indices)

{0: ' ', 1: '+', 2: '0', 3: '1', 4: '2', 5: '3', 6: '4', 7: '5', 8: '6', 9: '7', 10: '8', 11: '9'}
{' ': 0, '+': 1, '0': 2, '1': 3, '2': 4, '3': 5, '4': 6, '5': 7, '6': 8, '7': 9, '8': 10, '9': 11}


# Data Generation

In [7]:
questions=[]
expected=[]
seen=set()
print('Generating data....')
while len(questions)<TRAINING_SIZE:
    f=lambda:int(''.join(np.random.choice(list('0123456789')) for i in range(np.random.randint(1,DIGITS+1))))
    a,b,c=f(),f(),f()
    key=tuple(sorted((a,b,c)))
    if key in seen:
        continue
    seen.add(key)
    q='{}+{}+{}'.format(a,b,c)
    query=q+' '*(MAXLEN-len(q))
    ans=str(a+b+c)
    ans+=' '*(DIGITS+1-len(ans))
    if REVERSE:
        query=query[::-1]
    questions.append(query)
    expected.append(ans)
print('Total addition questions:',len(questions))

Generating data....
Total addition questions: 80000


In [8]:
print(questions[:5],expected[:5])

['552+1+99   ', '2+879+6    ', '509+0+9    ', '495+4+87   ', '305+922+462'] ['652 ', '887 ', '518 ', '586 ', '1689']


# Processing

In [9]:
print('Vectorization....')
x=np.zeros((len(questions),MAXLEN,len(chars)),dtype=np.bool)
y=np.zeros((len(expected),DIGITS+1,len(chars)),dtype=np.bool)
for i,sentence in enumerate(questions):
    x[i]=ctable.encode(sentence,MAXLEN)
for i,sentence in enumerate(expected):
    y[i]=ctable.encode(sentence,DIGITS+1)

Vectorization....


In [10]:
indices=np.arange(len(y))
np.random.shuffle(indices)
x=x[indices]
y=y[indices]

#train_test_split
train_x=x[:20000]
train_y=y[:20000]
test_x=x[20000:]
test_y=y[20000:]

split_at=len(train_x)-len(train_x)//10
(x_train,x_val)=train_x[:split_at],train_x[split_at:]
(y_train,y_val)=train_y[:split_at],train_y[split_at:]

print('Training Data:')
print(x_train.shape)
print(y_train.shape)

print('Validation Data:')
print(x_val.shape)
print(y_val.shape)

print('Testing Date:')
print(test_x.shape)
print(test_y.shape)

Training Data:
(18000, 11, 12)
(18000, 4, 12)
Validation Data:
(2000, 11, 12)
(2000, 4, 12)
Testing Date:
(60000, 11, 12)
(60000, 4, 12)


In [11]:
print('input: ',x_train[:3],'\n\n','label: ',y_train[:3])

input:  [[[False False False False  True False False False False False False
   False]
  [False  True False False False False False False False False False
   False]
  [False False False False False False False False False  True False
   False]
  [False  True False False False False False False False False False
   False]
  [False False False False False  True False False False False False
   False]
  [False False False False False  True False False False False False
   False]
  [False False False False False False False False  True False False
   False]
  [ True False False False False False False False False False False
   False]
  [ True False False False False False False False False False False
   False]
  [ True False False False False False False False False False False
   False]
  [ True False False False False False False False False False False
   False]]

 [[False False False False False False False False False False False
    True]
  [False False  True False False False Fal

# Build Model

In [12]:
print('Build model...')

model = Sequential()
model.add(RNN(HIDDEN_SIZE, input_shape=(MAXLEN, len(chars))))
model.add(layers.RepeatVector(DIGITS + 1))
for _ in range(LAYERS):
    model.add(RNN(HIDDEN_SIZE, return_sequences=True))
model.add(layers.TimeDistributed(layers.Dense(len(chars), activation='softmax')))
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
model.summary()

Build model...
Instructions for updating:
Colocations handled automatically by placer.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_1 (LSTM)                (None, 128)               72192     
_________________________________________________________________
repeat_vector_1 (RepeatVecto (None, 4, 128)            0         
_________________________________________________________________
lstm_2 (LSTM)                (None, 4, 128)            131584    
_________________________________________________________________
time_distributed_1 (TimeDist (None, 4, 12)             1548      
Total params: 205,324
Trainable params: 205,324
Non-trainable params: 0
_________________________________________________________________


# Training and Testing

### iteration=100

In [13]:
for iteration in range(100):
    print()
    print('-' * 50)
    print('Iteration', iteration)
    model.fit(x_train, y_train,
              batch_size=BATCH_SIZE,
              epochs=1,
              validation_data=(x_val, y_val))
    for i in range(10):
        ind = np.random.randint(0, len(x_val))
        rowx, rowy = x_val[np.array([ind])], y_val[np.array([ind])]
        preds = model.predict_classes(rowx, verbose=0)
        q = ctable.decode(rowx[0])
        correct = ctable.decode(rowy[0])
        guess = ctable.decode(preds[0], calc_argmax=False)
        print('Q', q[::-1] if REVERSE else q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)


--------------------------------------------------
Iteration 0
Instructions for updating:
Use tf.cast instead.
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 6s 320us/step - loss: 1.9867 - acc: 0.3169 - val_loss: 1.8248 - val_acc: 0.3557
Q 43+61+40    T 144  ☒ 100 
Q 45+21+164   T 230  ☒ 100 
Q 3+156+202   T 361  ☒ 100 
Q 320+9+13    T 342  ☒ 100 
Q 285+8+1     T 294  ☒ 10  
Q 7+354+4     T 365  ☒ 10  
Q 7+655+2     T 664  ☒ 10  
Q 836+5+2     T 843  ☒ 10  
Q 29+915+4    T 948  ☒ 100 
Q 533+642+1   T 1176 ☒ 100 

--------------------------------------------------
Iteration 1
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 184us/step - loss: 1.8190 - acc: 0.3588 - val_loss: 1.8146 - val_acc: 0.3582
Q 534+215+54  T 803  ☒ 103 
Q 9+816+3     T 828  ☒ 108 
Q 332+304+939 T 1575 ☒ 110 
Q 844+96+965  T 1905 ☒ 1108
Q 59+35+118   T 212  ☒ 108 
Q 48+472+8    T 528  ☒ 108 
Q 1+

18000/18000 [==============================] - 3s 183us/step - loss: 1.3627 - acc: 0.4857 - val_loss: 1.3505 - val_acc: 0.4904
Q 375+32+5    T 412  ☒ 433 
Q 1+35+99     T 135  ☒ 133 
Q 557+1+409   T 967  ☒ 100 
Q 33+757+123  T 913  ☒ 800 
Q 29+915+4    T 948  ☒ 900 
Q 666+34+27   T 727  ☒ 770 
Q 33+283+804  T 1120 ☒ 1001
Q 328+21+73   T 422  ☒ 300 
Q 693+4+1     T 698  ☒ 721 
Q 1+670+96    T 767  ☒ 770 

--------------------------------------------------
Iteration 14
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 184us/step - loss: 1.3238 - acc: 0.4983 - val_loss: 1.3347 - val_acc: 0.4919
Q 837+7+1     T 845  ☒ 883 
Q 15+386+82   T 483  ☒ 493 
Q 9+1+448     T 458  ☒ 452 
Q 0+47+97     T 144  ☒ 156 
Q 59+20+2     T 81   ☒ 73  
Q 886+0+17    T 903  ☒ 986 
Q 16+15+737   T 768  ☒ 793 
Q 857+636+4   T 1497 ☒ 1394
Q 4+634+6     T 644  ☒ 554 
Q 364+95+13   T 472  ☒ 404 

--------------------------------------------------
Iteration 

Q 92+19+20    T 131  ☑ 131 
Q 509+75+904  T 1488 ☒ 1400
Q 7+9+645     T 661  ☒ 640 
Q 748+303+6   T 1057 ☒ 1005
Q 83+376+67   T 526  ☒ 520 
Q 957+8+301   T 1266 ☒ 1310
Q 459+160+339 T 958  ☒ 900 
Q 10+0+602    T 612  ☒ 593 
Q 508+388+1   T 897  ☒ 850 
Q 5+35+93     T 133  ☒ 132 

--------------------------------------------------
Iteration 27
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 196us/step - loss: 1.1093 - acc: 0.5819 - val_loss: 1.1410 - val_acc: 0.5599
Q 3+50+7      T 60   ☒ 54  
Q 52+508+48   T 608  ☒ 671 
Q 634+7+42    T 683  ☒ 611 
Q 40+8+813    T 861  ☒ 817 
Q 7+460+0     T 467  ☒ 464 
Q 947+364+42  T 1353 ☒ 1331
Q 47+1+560    T 608  ☒ 651 
Q 54+411+26   T 491  ☒ 471 
Q 8+38+452    T 498  ☒ 473 
Q 300+65+153  T 518  ☒ 411 

--------------------------------------------------
Iteration 28
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 186us/step - lo

18000/18000 [==============================] - 3s 189us/step - loss: 1.0038 - acc: 0.6217 - val_loss: 1.0623 - val_acc: 0.5921
Q 2+6+614     T 622  ☒ 624 
Q 832+67+3    T 902  ☒ 910 
Q 40+62+9     T 111  ☑ 111 
Q 7+692+6     T 705  ☒ 703 
Q 613+305+1   T 919  ☒ 981 
Q 61+2+2      T 65   ☒ 61  
Q 267+6+38    T 311  ☒ 310 
Q 7+746+980   T 1733 ☒ 1743
Q 1+228+49    T 278  ☒ 280 
Q 1+783+8     T 792  ☒ 791 

--------------------------------------------------
Iteration 41
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 189us/step - loss: 0.9960 - acc: 0.6251 - val_loss: 1.0869 - val_acc: 0.5783
Q 21+85+1     T 107  ☒ 104 
Q 889+687+5   T 1581 ☒ 1593
Q 17+79+3     T 99   ☒ 90  
Q 3+381+644   T 1028 ☒ 100 
Q 602+1+7     T 610  ☒ 624 
Q 1+43+1      T 45   ☒ 42  
Q 491+9+6     T 506  ☒ 502 
Q 2+26+56     T 84   ☒ 86  
Q 271+5+87    T 363  ☒ 354 
Q 557+1+409   T 967  ☒ 847 

--------------------------------------------------
Iteration 

Q 71+25+921   T 1017 ☒ 1031
Q 19+4+55     T 78   ☒ 72  
Q 92+6+742    T 840  ☒ 821 
Q 75+736+9    T 820  ☒ 818 
Q 98+393+112  T 603  ☒ 518 
Q 842+915+28  T 1785 ☒ 1768
Q 932+0+4     T 936  ☒ 940 
Q 338+59+504  T 901  ☒ 848 
Q 507+841+5   T 1353 ☒ 1388
Q 0+800+669   T 1469 ☒ 1476

--------------------------------------------------
Iteration 54
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 193us/step - loss: 0.9193 - acc: 0.6541 - val_loss: 1.0007 - val_acc: 0.6163
Q 8+5+472     T 485  ☒ 486 
Q 815+2+533   T 1350 ☒ 1355
Q 411+4+937   T 1352 ☒ 1375
Q 416+7+80    T 503  ☒ 504 
Q 9+37+0      T 46   ☒ 45  
Q 87+499+230  T 816  ☒ 815 
Q 9+872+0     T 881  ☒ 880 
Q 9+67+152    T 228  ☒ 239 
Q 919+545+3   T 1467 ☒ 1460
Q 69+610+61   T 740  ☒ 755 

--------------------------------------------------
Iteration 55
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 189us/step - lo

18000/18000 [==============================] - 3s 191us/step - loss: 0.8403 - acc: 0.6895 - val_loss: 0.9518 - val_acc: 0.6385
Q 241+882+667 T 1790 ☒ 1789
Q 508+388+1   T 897  ☒ 880 
Q 54+6+37     T 97   ☑ 97  
Q 5+1+41      T 47   ☒ 48  
Q 4+30+386    T 420  ☒ 426 
Q 974+93+315  T 1382 ☒ 1373
Q 764+4+84    T 852  ☒ 840 
Q 85+33+325   T 443  ☑ 443 
Q 4+9+914     T 927  ☒ 922 
Q 1+43+1      T 45   ☑ 45  

--------------------------------------------------
Iteration 68
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 194us/step - loss: 0.8233 - acc: 0.6969 - val_loss: 0.9835 - val_acc: 0.6248
Q 0+569+12    T 581  ☒ 579 
Q 22+12+5     T 39   ☑ 39  
Q 666+34+27   T 727  ☒ 725 
Q 553+68+325  T 946  ☒ 949 
Q 965+4+4     T 973  ☒ 976 
Q 5+3+805     T 813  ☒ 819 
Q 266+19+56   T 341  ☒ 350 
Q 51+8+3      T 62   ☒ 64  
Q 520+312+2   T 834  ☒ 860 
Q 472+85+9    T 566  ☒ 560 

--------------------------------------------------
Iteration 

Q 25+90+312   T 427  ☒ 443 
Q 1+70+7      T 78   ☑ 78  
Q 437+8+7     T 452  ☒ 446 
Q 74+88+9     T 171  ☒ 170 
Q 1+928+58    T 987  ☒ 996 
Q 65+66+6     T 137  ☒ 130 
Q 77+4+20     T 101  ☑ 101 
Q 34+3+820    T 857  ☒ 850 
Q 94+998+332  T 1424 ☒ 1393
Q 34+879+9    T 922  ☒ 926 

--------------------------------------------------
Iteration 81
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 189us/step - loss: 0.7665 - acc: 0.7188 - val_loss: 0.9727 - val_acc: 0.6392
Q 27+7+307    T 341  ☑ 341 
Q 983+8+1     T 992  ☒ 981 
Q 66+92+0     T 158  ☒ 151 
Q 454+96+57   T 607  ☒ 591 
Q 488+483+7   T 978  ☒ 957 
Q 529+44+93   T 666  ☒ 645 
Q 27+99+5     T 131  ☒ 133 
Q 705+499+7   T 1211 ☑ 1211
Q 821+331+977 T 2129 ☒ 2031
Q 5+78+5      T 88   ☒ 89  

--------------------------------------------------
Iteration 82
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 182us/step - lo

18000/18000 [==============================] - 3s 189us/step - loss: 0.7347 - acc: 0.7292 - val_loss: 0.9667 - val_acc: 0.6450
Q 7+740+4     T 751  ☒ 756 
Q 7+500+52    T 559  ☒ 558 
Q 848+393+876 T 2117 ☒ 2039
Q 79+62+68    T 209  ☒ 207 
Q 8+7+58      T 73   ☑ 73  
Q 3+62+975    T 1040 ☒ 1044
Q 905+5+5     T 915  ☒ 913 
Q 1+971+9     T 981  ☑ 981 
Q 320+9+13    T 342  ☒ 346 
Q 91+21+78    T 190  ☒ 188 

--------------------------------------------------
Iteration 95
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 186us/step - loss: 0.6985 - acc: 0.7475 - val_loss: 0.9841 - val_acc: 0.6417
Q 79+920+77   T 1076 ☒ 1088
Q 8+324+2     T 334  ☒ 338 
Q 97+10+947   T 1054 ☒ 1039
Q 17+796+29   T 842  ☒ 839 
Q 61+55+2     T 118  ☒ 129 
Q 64+393+22   T 479  ☒ 488 
Q 723+7+3     T 733  ☒ 734 
Q 90+353+821  T 1264 ☒ 1244
Q 9+33+560    T 602  ☒ 603 
Q 965+546+9   T 1520 ☒ 1498

--------------------------------------------------
Iteration 

In [14]:
print("MSG : Prediction")

pred_y=model.predict_classes(test_x,verbose=0)
right=0
for i in range(len(test_x)):
    q=ctable.decode(test_x[i])
    correct=ctable.decode(test_y[i])
    pred=ctable.decode(pred_y[i], calc_argmax=False)
    print('Q', q[::-1] if REVERSE else q, end=' ')
    print('T', correct, end=' ')
    if correct==pred:
        right+=1
        print(colors.ok+'☑' + colors.close, end=' ')
    else:
        print(colors.fail + '☒' + colors.close, end=' ')
    print(pred)
print('accuracy=',(right/len(test_x))*100,'%')

MSG : Prediction
Q 462+59+741  T 1262 ☒ 1254
Q 41+94+69    T 204  ☒ 205 
Q 13+28+9     T 50   ☒ 52  
Q 15+21+889   T 925  ☑ 925 
Q 551+47+4    T 602  ☒ 600 
Q 153+1+1     T 155  ☒ 153 
Q 83+734+226  T 1043 ☒ 1029
Q 48+99+441   T 588  ☒ 558 
Q 53+55+59    T 167  ☑ 167 
Q 22+450+6    T 478  ☒ 482 
Q 2+94+789    T 885  ☒ 887 
Q 0+8+446     T 454  ☒ 451 
Q 634+15+760  T 1409 ☒ 1450
Q 86+932+2    T 1020 ☒ 1011
Q 443+4+79    T 526  ☒ 530 
Q 15+65+1     T 81   ☒ 83  
Q 426+13+96   T 535  ☒ 510 
Q 2+102+0     T 104  ☒ 11  
Q 7+234+672   T 913  ☒ 922 
Q 67+28+230   T 325  ☒ 324 
Q 21+72+533   T 626  ☒ 624 
Q 9+326+8     T 343  ☒ 345 
Q 141+68+61   T 270  ☒ 260 
Q 866+170+4   T 1040 ☑ 1040
Q 77+0+676    T 753  ☒ 741 
Q 29+722+212  T 963  ☒ 983 
Q 945+620+3   T 1568 ☒ 1561
Q 476+26+1    T 503  ☒ 495 
Q 77+844+30   T 951  ☒ 952 
Q 1+499+0     T 500  ☒ 497 
Q 3+3+985     T 991  ☒ 990 
Q 87+65+430   T 582  ☒ 560 
Q 5+50+826    T 881  ☒ 880 
Q 46+34+309   T 389  ☒ 300 
Q 3+298+67    T 368  ☒ 374 
Q 9

Q 27+0+48     T 75   ☒ 73  
Q 1+7+157     T 165  ☒ 162 
Q 481+67+45   T 593  ☒ 594 
Q 34+107+4    T 145  ☑ 145 
Q 4+79+4      T 87   ☑ 87  
Q 83+220+237  T 540  ☒ 446 
Q 48+87+961   T 1096 ☒ 1102
Q 74+8+13     T 95   ☒ 94  
Q 71+34+405   T 510  ☒ 515 
Q 370+735+933 T 2038 ☒ 1985
Q 989+1+8     T 998  ☒ 992 
Q 40+1+25     T 66   ☒ 68  
Q 8+63+670    T 741  ☑ 741 
Q 104+765+611 T 1480 ☒ 1541
Q 4+568+38    T 610  ☒ 623 
Q 780+80+8    T 868  ☒ 872 
Q 116+49+36   T 201  ☒ 190 
Q 88+231+3    T 322  ☒ 315 
Q 145+39+272  T 456  ☒ 460 
Q 35+954+83   T 1072 ☒ 1079
Q 4+32+486    T 522  ☒ 523 
Q 32+486+32   T 550  ☒ 559 
Q 784+39+79   T 902  ☒ 900 
Q 44+9+93     T 146  ☒ 145 
Q 33+6+0      T 39   ☑ 39  
Q 2+656+2     T 660  ☒ 661 
Q 883+1+8     T 892  ☒ 899 
Q 174+416+80  T 670  ☒ 650 
Q 8+638+8     T 654  ☒ 655 
Q 349+20+51   T 420  ☒ 428 
Q 4+0+62      T 66   ☒ 67  
Q 7+548+773   T 1328 ☒ 1340
Q 750+29+699  T 1478 ☒ 1450
Q 604+7+561   T 1172 ☒ 1185
Q 5+12+7      T 24   ☒ 25  
Q 3+0+191     T 194 

Q 450+37+70   T 557  ☒ 551 
Q 73+345+23   T 441  ☑ 441 
Q 933+6+274   T 1213 ☒ 1202
Q 168+493+46  T 707  ☒ 790 
Q 14+46+395   T 455  ☒ 471 
Q 7+4+330     T 341  ☒ 349 
Q 50+73+1     T 124  ☒ 130 
Q 61+16+13    T 90   ☒ 91  
Q 100+6+35    T 141  ☒ 139 
Q 631+947+2   T 1580 ☒ 1500
Q 39+50+4     T 93   ☒ 94  
Q 92+428+774  T 1294 ☒ 1254
Q 8+6+604     T 618  ☒ 622 
Q 231+7+3     T 241  ☒ 244 
Q 19+36+22    T 77   ☒ 76  
Q 6+38+451    T 495  ☒ 491 
Q 923+725+0   T 1648 ☒ 1644
Q 34+54+33    T 121  ☒ 122 
Q 7+57+582    T 646  ☒ 651 
Q 87+5+44     T 136  ☒ 134 
Q 76+52+8     T 136  ☒ 132 
Q 474+139+339 T 952  ☒ 941 
Q 285+578+3   T 866  ☒ 874 
Q 89+9+23     T 121  ☒ 125 
Q 8+757+8     T 773  ☒ 763 
Q 78+670+2    T 750  ☒ 751 
Q 3+22+699    T 724  ☒ 723 
Q 61+296+10   T 367  ☒ 375 
Q 371+7+9     T 387  ☒ 388 
Q 553+1+34    T 588  ☒ 594 
Q 631+5+560   T 1196 ☒ 1195
Q 7+937+731   T 1675 ☒ 1693
Q 6+789+255   T 1050 ☒ 1040
Q 33+339+57   T 429  ☒ 425 
Q 444+69+9    T 522  ☒ 525 
Q 98+277+967  T 1342

Q 500+38+66   T 604  ☒ 600 
Q 68+949+5    T 1022 ☑ 1022
Q 4+618+79    T 701  ☒ 715 
Q 6+82+10     T 98   ☒ 99  
Q 358+96+975  T 1429 ☒ 1405
Q 901+4+600   T 1505 ☒ 1549
Q 2+368+903   T 1273 ☒ 1240
Q 750+864+3   T 1617 ☒ 1644
Q 79+2+3      T 84   ☒ 85  
Q 70+332+7    T 409  ☒ 405 
Q 72+9+57     T 138  ☒ 145 
Q 404+8+8     T 420  ☒ 425 
Q 73+920+263  T 1256 ☒ 1239
Q 564+518+4   T 1086 ☒ 1087
Q 99+829+83   T 1011 ☒ 1018
Q 8+56+40     T 104  ☑ 104 
Q 29+9+401    T 439  ☒ 449 
Q 17+8+95     T 120  ☒ 125 
Q 535+693+26  T 1254 ☒ 1250
Q 51+391+859  T 1301 ☒ 1250
Q 54+92+821   T 967  ☒ 965 
Q 69+5+244    T 318  ☒ 319 
Q 19+66+3     T 88   ☒ 89  
Q 7+584+2     T 593  ☒ 594 
Q 492+7+364   T 863  ☒ 840 
Q 77+7+761    T 845  ☒ 847 
Q 0+1+87      T 88   ☒ 85  
Q 433+2+774   T 1209 ☒ 1206
Q 131+7+175   T 313  ☒ 397 
Q 771+34+5    T 810  ☒ 803 
Q 19+438+13   T 470  ☒ 472 
Q 819+564+54  T 1437 ☒ 1455
Q 654+96+622  T 1372 ☒ 1374
Q 0+78+404    T 482  ☒ 483 
Q 3+5+218     T 226  ☒ 230 
Q 89+8+80     T 177 

Q 3+57+619    T 679  ☒ 685 
Q 222+56+59   T 337  ☒ 325 
Q 4+321+552   T 877  ☒ 825 
Q 935+6+78    T 1019 ☒ 1020
Q 810+246+1   T 1057 ☒ 1044
Q 434+3+521   T 958  ☒ 923 
Q 5+5+544     T 554  ☒ 559 
Q 5+605+163   T 773  ☑ 773 
Q 478+78+759  T 1315 ☒ 1340
Q 642+1+105   T 748  ☒ 753 
Q 333+4+0     T 337  ☒ 330 
Q 317+379+7   T 703  ☒ 628 
Q 789+87+43   T 919  ☒ 910 
Q 93+200+6    T 299  ☒ 300 
Q 737+221+33  T 991  ☒ 1000
Q 4+369+336   T 709  ☒ 625 
Q 45+725+62   T 832  ☑ 832 
Q 710+3+3     T 716  ☒ 715 
Q 86+52+4     T 142  ☒ 145 
Q 4+956+7     T 967  ☒ 961 
Q 82+7+6      T 95   ☒ 96  
Q 27+64+50    T 141  ☑ 141 
Q 4+50+0      T 54   ☒ 55  
Q 40+756+6    T 802  ☒ 709 
Q 511+54+4    T 569  ☒ 562 
Q 23+34+2     T 59   ☒ 57  
Q 84+0+90     T 174  ☒ 171 
Q 8+6+785     T 799  ☒ 890 
Q 11+9+900    T 920  ☑ 920 
Q 461+3+59    T 523  ☑ 523 
Q 6+38+57     T 101  ☒ 100 
Q 955+30+60   T 1045 ☒ 1048
Q 889+96+748  T 1733 ☒ 1757
Q 92+91+4     T 187  ☒ 188 
Q 5+944+32    T 981  ☒ 980 
Q 37+20+516   T 573 

...

Q 146+66+36   T 248  ☒ 244 
Q 496+65+296  T 857  ☒ 887 
Q 748+68+6    T 822  ☒ 827 
Q 676+7+0     T 683  ☒ 687 
Q 254+22+43   T 319  ☒ 325 
Q 31+9+7      T 47   ☒ 45  
Q 85+4+518    T 607  ☒ 611 
Q 6+863+9     T 878  ☒ 887 
Q 36+8+408    T 452  ☒ 449 
Q 9+739+58    T 806  ☒ 813 
Q 8+244+0     T 252  ☒ 258 
Q 349+7+8     T 364  ☒ 365 
Q 855+8+59    T 922  ☒ 910 
Q 943+87+0    T 1030 ☒ 1038
Q 49+152+56   T 257  ☒ 253 
Q 584+278+6   T 868  ☒ 876 
Q 3+649+74    T 726  ☒ 725 
Q 1+6+889     T 896  ☒ 897 
Q 20+173+902  T 1095 ☒ 1121
Q 5+53+16     T 74   ☒ 75  
Q 327+0+6     T 333  ☒ 332 
Q 955+414+3   T 1372 ☒ 1380
Q 417+18+25   T 460  ☒ 462 
Q 82+43+658   T 783  ☒ 784 
Q 0+584+9     T 593  ☒ 594 
Q 84+16+782   T 882  ☒ 877 
Q 4+808+20    T 832  ☒ 829 
Q 662+14+2    T 678  ☒ 681 
Q 91+635+0    T 726  ☒ 728 
Q 190+39+327  T 556  ☒ 541 
Q 54+2+92     T 148  ☑ 148 
Q 33+78+3     T 114  ☒ 113 
Q 467+5+371   T 843  ☒ 840 
Q 0+72+929    T 1001 ☒ 1004
Q 992+670+75  T 1737 ☒ 1724
Q 1+31+961    T 993 

Q 102+33+849  T 984  ☒ 982 
Q 9+672+1     T 682  ☒ 683 
Q 514+8+13    T 535  ☒ 539 
Q 96+0+76     T 172  ☒ 178 
Q 440+290+619 T 1349 ☒ 1328
Q 6+540+165   T 711  ☒ 718 
Q 6+234+25    T 265  ☒ 269 
Q 117+84+10   T 211  ☒ 215 
Q 954+38+397  T 1389 ☒ 1380
Q 25+33+63    T 121  ☒ 120 
Q 501+7+35    T 543  ☒ 551 
Q 362+0+60    T 422  ☒ 414 
Q 52+8+2      T 62   ☒ 64  
Q 729+4+51    T 784  ☒ 785 
Q 87+6+525    T 618  ☒ 625 
Q 44+67+6     T 117  ☒ 119 
Q 80+55+31    T 166  ☒ 161 
Q 691+10+3    T 704  ☒ 705 
Q 9+71+51     T 131  ☑ 131 
Q 3+49+12     T 64   ☒ 65  
Q 12+842+46   T 900  ☒ 901 
Q 388+9+676   T 1073 ☒ 1052
Q 188+4+45    T 237  ☒ 234 
Q 40+7+40     T 87   ☒ 89  
Q 79+3+156    T 238  ☒ 241 
Q 922+8+57    T 987  ☒ 990 
Q 6+5+573     T 584  ☒ 581 
Q 75+244+498  T 817  ☒ 788 
Q 630+49+31   T 710  ☒ 715 
Q 11+85+3     T 99   ☒ 100 
Q 59+948+8    T 1015 ☒ 1012
Q 17+93+60    T 170  ☑ 170 
Q 8+53+623    T 684  ☒ 685 
Q 83+341+106  T 530  ☒ 576 
Q 10+175+1    T 186  ☒ 185 
Q 688+530+9   T 1227

Q 13+86+187   T 286  ☒ 287 
Q 61+891+83   T 1035 ☒ 1010
Q 85+934+621  T 1640 ☒ 1622
Q 649+2+5     T 656  ☒ 651 
Q 4+81+145    T 230  ☒ 229 
Q 18+85+6     T 109  ☑ 109 
Q 28+8+12     T 48   ☑ 48  
Q 486+140+20  T 646  ☒ 640 
Q 1+9+32      T 42   ☑ 42  
Q 611+985+303 T 1899 ☒ 1961
Q 289+357+54  T 700  ☒ 687 
Q 28+9+734    T 771  ☒ 783 
Q 8+887+807   T 1702 ☒ 1690
Q 644+852+193 T 1689 ☒ 1641
Q 4+284+7     T 295  ☒ 292 
Q 21+4+540    T 565  ☒ 572 
Q 19+3+44     T 66   ☒ 68  
Q 4+68+21     T 93   ☒ 94  
Q 617+475+429 T 1521 ☒ 1510
Q 713+0+67    T 780  ☒ 794 
Q 839+1+8     T 848  ☒ 847 
Q 4+8+626     T 638  ☒ 630 
Q 73+6+8      T 87   ☒ 86  
Q 7+219+9     T 235  ☒ 239 
Q 554+75+8    T 637  ☒ 646 
Q 278+41+5    T 324  ☒ 325 
Q 9+5+770     T 784  ☒ 785 
Q 8+25+17     T 50   ☒ 59  
Q 4+8+204     T 216  ☒ 210 
Q 9+86+689    T 784  ☒ 785 
Q 35+9+13     T 57   ☒ 56  
Q 13+72+2     T 87   ☒ 89  
Q 325+33+86   T 444  ☒ 440 
Q 6+1+337     T 344  ☒ 345 
Q 37+77+37    T 151  ☒ 145 
Q 357+2+58    T 417 

Q 436+26+931  T 1393 ☒ 1300
Q 64+279+374  T 717  ☒ 721 
Q 7+1+934     T 942  ☒ 930 
Q 7+871+52    T 930  ☑ 930 
Q 940+8+71    T 1019 ☒ 1010
Q 8+9+78      T 95   ☒ 97  
Q 23+50+7     T 80   ☒ 83  
Q 84+0+372    T 456  ☒ 468 
Q 9+652+66    T 727  ☒ 725 
Q 514+8+2     T 524  ☑ 524 
Q 94+22+366   T 482  ☒ 470 
Q 2+941+1     T 944  ☒ 940 
Q 0+334+678   T 1012 ☒ 1002
Q 269+2+4     T 275  ☒ 277 
Q 81+2+139    T 222  ☒ 229 
Q 575+55+6    T 636  ☑ 636 
Q 38+125+6    T 169  ☒ 175 
Q 88+62+47    T 197  ☒ 107 
Q 138+60+50   T 248  ☒ 244 
Q 5+7+169     T 181  ☒ 183 
Q 7+37+2      T 46   ☒ 45  
Q 96+18+11    T 125  ☒ 129 
Q 6+186+0     T 192  ☒ 193 
Q 0+601+51    T 652  ☒ 651 
Q 13+0+344    T 357  ☒ 353 
Q 9+62+6      T 77   ☒ 71  
Q 655+7+88    T 750  ☑ 750 
Q 64+869+18   T 951  ☒ 955 
Q 474+75+31   T 580  ☒ 560 
Q 364+3+888   T 1255 ☒ 1244
Q 202+3+3     T 208  ☒ 210 
Q 8+937+534   T 1479 ☒ 1459
Q 232+9+260   T 501  ☒ 591 
Q 597+0+1     T 598  ☒ 691 
Q 27+658+5    T 690  ☒ 691 
Q 115+17+36   T 168 

Q 772+681+1   T 1454 ☒ 1494
Q 79+311+38   T 428  ☒ 435 
Q 97+372+169  T 638  ☒ 621 
Q 615+48+3    T 666  ☒ 661 
Q 7+295+148   T 450  ☒ 438 
Q 353+322+2   T 677  ☒ 690 
Q 20+622+4    T 646  ☒ 641 
Q 12+12+5     T 29   ☒ 32  
Q 798+4+489   T 1291 ☒ 1260
Q 54+854+9    T 917  ☒ 923 
Q 68+79+20    T 167  ☒ 161 
Q 0+238+1     T 239  ☒ 246 
Q 654+95+745  T 1494 ☒ 1510
Q 86+741+48   T 875  ☒ 884 
Q 15+937+240  T 1192 ☒ 1140
Q 43+253+84   T 380  ☒ 373 
Q 789+617+8   T 1414 ☒ 1323
Q 82+98+2     T 182  ☒ 181 
Q 9+9+434     T 452  ☒ 451 
Q 228+79+99   T 406  ☒ 415 
Q 500+789+87  T 1376 ☒ 1357
Q 3+422+0     T 425  ☒ 408 
Q 123+1+3     T 127  ☒ 129 
Q 91+293+2    T 386  ☒ 394 
Q 95+389+61   T 545  ☒ 524 
Q 51+79+9     T 139  ☒ 141 
Q 98+536+64   T 698  ☒ 609 
Q 8+469+95    T 572  ☒ 573 
Q 8+42+31     T 81   ☒ 83  
Q 4+27+490    T 521  ☒ 524 
Q 1+54+724    T 779  ☒ 775 
Q 867+21+22   T 910  ☒ 918 
Q 6+52+21     T 79   ☒ 75  
Q 409+185+9   T 603  ☒ 600 
Q 215+880+3   T 1098 ☒ 1100
Q 627+64+4    T 695 

### iteration=200

In [15]:
print('Build model...')

model = Sequential()
model.add(RNN(HIDDEN_SIZE, input_shape=(MAXLEN, len(chars))))
model.add(layers.RepeatVector(DIGITS + 1))
for _ in range(LAYERS):
    model.add(RNN(HIDDEN_SIZE, return_sequences=True))
model.add(layers.TimeDistributed(layers.Dense(len(chars), activation='softmax')))
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
model.summary()
#training
for iteration in range(200):
    print()
    print('-' * 50)
    print('Iteration', iteration)
    model.fit(x_train, y_train,
              batch_size=BATCH_SIZE,
              epochs=1,
              validation_data=(x_val, y_val))
    for i in range(10):
        ind = np.random.randint(0, len(x_val))
        rowx, rowy = x_val[np.array([ind])], y_val[np.array([ind])]
        preds = model.predict_classes(rowx, verbose=0)
        q = ctable.decode(rowx[0])
        correct = ctable.decode(rowy[0])
        guess = ctable.decode(preds[0], calc_argmax=False)
        print('Q', q[::-1] if REVERSE else q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)

Build model...
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_3 (LSTM)                (None, 128)               72192     
_________________________________________________________________
repeat_vector_2 (RepeatVecto (None, 4, 128)            0         
_________________________________________________________________
lstm_4 (LSTM)                (None, 4, 128)            131584    
_________________________________________________________________
time_distributed_2 (TimeDist (None, 4, 12)             1548      
Total params: 205,324
Trainable params: 205,324
Non-trainable params: 0
_________________________________________________________________

--------------------------------------------------
Iteration 0
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 6s 338us/step - loss: 1.9758 - acc: 0.3207 - val_loss: 1.8366 - val_acc: 0.3499
Q 4

Q 748+303+6   T 1057 ☒ 100 

--------------------------------------------------
Iteration 12
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 202us/step - loss: 1.4343 - acc: 0.4612 - val_loss: 1.4096 - val_acc: 0.4693
Q 182+54+510  T 746  ☒ 590 
Q 919+545+3   T 1467 ☒ 1545
Q 81+319+707  T 1107 ☒ 1001
Q 9+28+73     T 110  ☒ 10  
Q 967+3+9     T 979  ☒ 900 
Q 34+879+9    T 922  ☒ 807 
Q 889+687+5   T 1581 ☒ 1545
Q 972+426+24  T 1422 ☒ 1747
Q 531+906+6   T 1443 ☒ 1307
Q 5+945+5     T 955  ☒ 907 

--------------------------------------------------
Iteration 13
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 200us/step - loss: 1.3771 - acc: 0.4813 - val_loss: 1.3579 - val_acc: 0.4840
Q 244+53+8    T 305  ☒ 337 
Q 61+303+974  T 1338 ☒ 1337
Q 7+27+46     T 80   ☒ 83  
Q 509+43+71   T 623  ☒ 677 
Q 2+90+8      T 100  ☑ 100 
Q 311+443+92  T 846  ☒ 900 
Q 6+31+126    T 163  ☒

18000/18000 [==============================] - 4s 208us/step - loss: 1.1138 - acc: 0.5804 - val_loss: 1.1673 - val_acc: 0.5483
Q 38+39+6     T 83   ☒ 85  
Q 59+3+187    T 249  ☒ 226 
Q 865+49+86   T 1000 ☒ 961 
Q 151+8+97    T 256  ☒ 236 
Q 629+3+4     T 636  ☒ 633 
Q 83+61+23    T 167  ☒ 161 
Q 37+221+6    T 264  ☒ 256 
Q 75+809+144  T 1028 ☒ 100 
Q 8+79+87     T 174  ☒ 163 
Q 9+28+73     T 110  ☒ 104 

--------------------------------------------------
Iteration 26
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 209us/step - loss: 1.1107 - acc: 0.5804 - val_loss: 1.1236 - val_acc: 0.5686
Q 817+36+6    T 859  ☒ 817 
Q 4+87+507    T 598  ☒ 554 
Q 80+496+8    T 584  ☒ 590 
Q 837+7+1     T 845  ☒ 848 
Q 7+639+291   T 937  ☒ 913 
Q 6+444+48    T 498  ☒ 473 
Q 0+8+850     T 858  ☒ 853 
Q 96+669+7    T 772  ☒ 797 
Q 792+95+727  T 1614 ☒ 1633
Q 50+22+7     T 79   ☒ 75  

--------------------------------------------------
Iteration 

Q 21+64+451   T 536  ☒ 524 
Q 11+6+65     T 82   ☑ 82  
Q 3+5+404     T 412  ☒ 413 
Q 49+219+91   T 359  ☒ 324 
Q 9+22+201    T 232  ☒ 226 
Q 95+1+4      T 100  ☒ 90  
Q 5+308+0     T 313  ☒ 316 
Q 2+240+698   T 940  ☒ 944 
Q 7+573+725   T 1305 ☒ 1222
Q 4+89+77     T 170  ☒ 161 

--------------------------------------------------
Iteration 39
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 208us/step - loss: 0.9552 - acc: 0.6434 - val_loss: 1.0264 - val_acc: 0.6045
Q 89+70+0     T 159  ☒ 155 
Q 190+75+853  T 1118 ☒ 1179
Q 152+841+41  T 1034 ☒ 1004
Q 527+472+0   T 999  ☒ 1003
Q 45+873+9    T 927  ☒ 936 
Q 656+41+20   T 717  ☒ 711 
Q 6+627+7     T 640  ☒ 638 
Q 804+8+2     T 814  ☒ 811 
Q 31+95+0     T 126  ☒ 125 
Q 506+369+623 T 1498 ☒ 1509

--------------------------------------------------
Iteration 40
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 200us/step - lo

18000/18000 [==============================] - 3s 191us/step - loss: 0.8767 - acc: 0.6747 - val_loss: 0.9509 - val_acc: 0.6357
Q 0+479+49    T 528  ☒ 524 
Q 72+83+9     T 164  ☒ 162 
Q 16+28+180   T 224  ☒ 216 
Q 0+27+400    T 427  ☒ 438 
Q 3+381+644   T 1028 ☒ 1001
Q 834+942+493 T 2269 ☒ 2163
Q 77+4+20     T 101  ☒ 10  
Q 5+65+140    T 210  ☒ 208 
Q 118+32+72   T 222  ☒ 224 
Q 559+56+8    T 623  ☒ 628 

--------------------------------------------------
Iteration 53
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 216us/step - loss: 0.8556 - acc: 0.6847 - val_loss: 0.9731 - val_acc: 0.6278
Q 55+1+448    T 504  ☒ 519 
Q 797+253+3   T 1053 ☒ 1044
Q 5+9+71      T 85   ☒ 80  
Q 1+87+961    T 1049 ☒ 1045
Q 13+902+348  T 1263 ☒ 1255
Q 968+210+969 T 2147 ☒ 1949
Q 9+2+797     T 808  ☒ 802 
Q 23+33+7     T 63   ☒ 65  
Q 968+210+969 T 2147 ☒ 1949
Q 62+9+11     T 82   ☒ 72  

--------------------------------------------------
Iteration 

...

18000/18000 [==============================] - 4s 200us/step - loss: 0.3700 - acc: 0.8796 - val_loss: 1.1703 - val_acc: 0.6627
Q 88+96+680   T 864  ☒ 879 
Q 739+282+715 T 1736 ☒ 1843
Q 79+920+77   T 1076 ☒ 1088
Q 5+23+916    T 944  ☒ 942 
Q 127+607+295 T 1029 ☒ 982 
Q 313+8+9     T 330  ☒ 331 
Q 5+465+23    T 493  ☒ 495 
Q 23+97+5     T 125  ☒ 126 
Q 3+8+432     T 443  ☒ 446 
Q 739+73+954  T 1766 ☒ 1771

--------------------------------------------------
Iteration 147
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 207us/step - loss: 0.3566 - acc: 0.8840 - val_loss: 1.1859 - val_acc: 0.6640
Q 92+2+61     T 155  ☒ 154 
Q 5+78+5      T 88   ☒ 89  
Q 98+87+6     T 191  ☒ 199 
Q 5+23+916    T 944  ☒ 943 
Q 11+114+10   T 135  ☒ 119 
Q 3+892+4     T 899  ☒ 904 
Q 568+3+54    T 625  ☑ 625 
Q 9+861+12    T 882  ☒ 886 
Q 175+985+583 T 1743 ☒ 1936
Q 3+233+4     T 240  ☒ 247 

--------------------------------------------------
Iteration

Q 5+23+585    T 613  ☒ 611 
Q 289+4+13    T 306  ☒ 304 
Q 20+240+65   T 325  ☑ 325 
Q 45+873+9    T 927  ☒ 926 
Q 63+739+6    T 808  ☒ 806 
Q 52+800+5    T 857  ☒ 853 
Q 23+696+4    T 723  ☒ 721 
Q 723+7+3     T 733  ☒ 735 
Q 576+689+3   T 1268 ☒ 1274
Q 99+256+955  T 1310 ☒ 1205

--------------------------------------------------
Iteration 160
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 196us/step - loss: 0.2771 - acc: 0.9166 - val_loss: 1.2656 - val_acc: 0.6635
Q 5+216+327   T 548  ☒ 463 
Q 6+802+2     T 810  ☒ 812 
Q 9+28+73     T 110  ☒ 119 
Q 98+7+54     T 159  ☒ 160 
Q 92+4+531    T 627  ☒ 539 
Q 30+778+2    T 810  ☑ 810 
Q 1+3+22      T 26   ☑ 26  
Q 9+8+46      T 63   ☒ 64  
Q 7+27+231    T 265  ☒ 264 
Q 377+95+63   T 535  ☒ 539 

--------------------------------------------------
Iteration 161
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 204us/step - 

Q 6+94+124    T 224  ☒ 213 
Q 3+74+77     T 154  ☒ 152 

--------------------------------------------------
Iteration 173
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 193us/step - loss: 0.2334 - acc: 0.9331 - val_loss: 1.4051 - val_acc: 0.6555
Q 892+8+800   T 1700 ☒ 1711
Q 58+523+13   T 594  ☒ 593 
Q 40+8+813    T 861  ☒ 857 
Q 514+892+211 T 1617 ☒ 1569
Q 64+57+909   T 1030 ☒ 1014
Q 3+892+4     T 899  ☒ 904 
Q 734+8+57    T 799  ☒ 798 
Q 52+14+335   T 401  ☒ 408 
Q 144+199+19  T 362  ☒ 308 
Q 826+2+56    T 884  ☒ 775 

--------------------------------------------------
Iteration 174
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 199us/step - loss: 0.2808 - acc: 0.9115 - val_loss: 1.4199 - val_acc: 0.6526
Q 892+8+800   T 1700 ☒ 1811
Q 10+0+602    T 612  ☒ 609 
Q 561+37+361  T 959  ☒ 1059
Q 834+4+959   T 1797 ☒ 1712
Q 34+218+998  T 1250 ☒ 1245
Q 971+622+592 T 2185

18000/18000 [==============================] - 4s 201us/step - loss: 0.1892 - acc: 0.9488 - val_loss: 1.4839 - val_acc: 0.6573
Q 4+87+507    T 598  ☒ 597 
Q 308+7+8     T 323  ☒ 329 
Q 86+152+3    T 241  ☒ 248 
Q 311+443+92  T 846  ☒ 880 
Q 1+21+80     T 102  ☒ 101 
Q 815+29+336  T 1180 ☒ 1175
Q 91+924+33   T 1048 ☒ 1049
Q 87+365+629  T 1081 ☒ 1087
Q 9+22+201    T 232  ☒ 236 
Q 2+29+16     T 47   ☑ 47  

--------------------------------------------------
Iteration 187
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 198us/step - loss: 0.2025 - acc: 0.9424 - val_loss: 1.4892 - val_acc: 0.6631
Q 37+9+674    T 720  ☒ 713 
Q 48+41+4     T 93   ☒ 94  
Q 184+0+8     T 192  ☒ 195 
Q 14+6+678    T 698  ☒ 690 
Q 67+292+55   T 414  ☒ 419 
Q 92+2+61     T 155  ☒ 154 
Q 9+414+638   T 1061 ☒ 1045
Q 5+308+0     T 313  ☒ 315 
Q 783+3+634   T 1420 ☒ 1429
Q 66+808+5    T 879  ☒ 876 

--------------------------------------------------
Iteration

Q 431+66+3    T 500  ☒ 402 
Q 143+5+14    T 162  ☒ 165 
Q 518+16+932  T 1466 ☒ 1372
Q 366+76+90   T 532  ☑ 532 
Q 614+2+19    T 635  ☒ 634 
Q 6+97+760    T 863  ☒ 862 
Q 715+849+8   T 1572 ☒ 1575
Q 584+5+3     T 592  ☒ 591 
Q 34+3+820    T 857  ☒ 859 
Q 0+81+9      T 90   ☒ 92  


In [16]:
print("MSG : Prediction")

pred_y=model.predict_classes(test_x,verbose=0)
right=0
for i in range(len(test_x)):
    q=ctable.decode(test_x[i])
    correct=ctable.decode(test_y[i])
    pred=ctable.decode(pred_y[i], calc_argmax=False)
    print('Q', q[::-1] if REVERSE else q, end=' ')
    print('T', correct, end=' ')
    if correct==pred:
        right+=1
        print(colors.ok+'☑' + colors.close, end=' ')
    else:
        print(colors.fail + '☒' + colors.close, end=' ')
    print(pred)
print('accuracy=',(right/len(test_x))*100,'%')

MSG : Prediction
Q 462+59+741  T 1262 ☑ 1262
Q 41+94+69    T 204  ☒ 196 
Q 13+28+9     T 50   ☒ 58  
Q 15+21+889   T 925  ☒ 939 
Q 551+47+4    T 602  ☒ 600 
Q 153+1+1     T 155  ☒ 150 
Q 83+734+226  T 1043 ☒ 943 
Q 48+99+441   T 588  ☒ 590 
Q 53+55+59    T 167  ☑ 167 
Q 22+450+6    T 478  ☒ 472 
Q 2+94+789    T 885  ☑ 885 
Q 0+8+446     T 454  ☒ 452 
Q 634+15+760  T 1409 ☒ 1407
Q 86+932+2    T 1020 ☒ 1028
Q 443+4+79    T 526  ☑ 526 
Q 15+65+1     T 81   ☒ 82  
Q 426+13+96   T 535  ☒ 530 
Q 2+102+0     T 104  ☒ 11  
Q 7+234+672   T 913  ☒ 918 
Q 67+28+230   T 325  ☒ 323 
Q 21+72+533   T 626  ☒ 611 
Q 9+326+8     T 343  ☒ 348 
Q 141+68+61   T 270  ☒ 263 
Q 866+170+4   T 1040 ☒ 1034
Q 77+0+676    T 753  ☒ 741 
Q 29+722+212  T 963  ☒ 961 
Q 945+620+3   T 1568 ☒ 1564
Q 476+26+1    T 503  ☒ 402 
Q 77+844+30   T 951  ☒ 945 
Q 1+499+0     T 500  ☒ 497 
Q 3+3+985     T 991  ☒ 990 
Q 87+65+430   T 582  ☒ 589 
Q 5+50+826    T 881  ☒ 876 
Q 46+34+309   T 389  ☒ 481 
Q 3+298+67    T 368  ☒ 366 
Q 9

Q 398+93+855  T 1346 ☒ 1305
Q 687+83+70   T 840  ☒ 869 
Q 547+369+0   T 916  ☒ 902 
Q 7+228+5     T 240  ☒ 241 
Q 776+20+9    T 805  ☒ 814 
Q 391+4+62    T 457  ☑ 457 
Q 44+5+15     T 64   ☑ 64  
Q 13+4+76     T 93   ☒ 92  
Q 4+69+4      T 77   ☒ 78  
Q 369+83+65   T 517  ☒ 506 
Q 78+20+5     T 103  ☑ 103 
Q 852+743+140 T 1735 ☒ 1737
Q 492+819+1   T 1312 ☒ 1310
Q 15+41+108   T 164  ☑ 164 
Q 4+88+76     T 168  ☒ 161 
Q 1+1+69      T 71   ☒ 72  
Q 7+24+7      T 38   ☑ 38  
Q 30+57+576   T 663  ☒ 666 
Q 205+425+3   T 633  ☒ 555 
Q 9+0+40      T 49   ☑ 49  
Q 428+588+32  T 1048 ☒ 1053
Q 502+124+99  T 725  ☒ 790 
Q 120+2+47    T 169  ☒ 175 
Q 53+164+0    T 217  ☒ 223 
Q 88+33+147   T 268  ☒ 271 
Q 16+7+9      T 32   ☒ 31  
Q 231+31+968  T 1230 ☒ 1233
Q 688+6+61    T 755  ☒ 750 
Q 37+720+28   T 785  ☒ 780 
Q 51+540+460  T 1051 ☒ 1043
Q 333+4+59    T 396  ☒ 390 
Q 41+3+4      T 48   ☑ 48  
Q 8+236+78    T 322  ☑ 322 
Q 2+4+99      T 105  ☑ 105 
Q 36+12+8     T 56   ☑ 56  
Q 27+0+48     T 75  

Q 2+846+80    T 928  ☒ 932 
Q 55+7+3      T 65   ☒ 64  
Q 32+6+85     T 123  ☑ 123 
Q 603+35+43   T 681  ☒ 673 
Q 3+4+20      T 27   ☒ 26  
Q 298+9+2     T 309  ☒ 300 
Q 6+118+9     T 133  ☒ 136 
Q 4+376+58    T 438  ☒ 437 
Q 93+50+481   T 624  ☑ 624 
Q 47+88+451   T 586  ☒ 596 
Q 32+206+827  T 1065 ☒ 1059
Q 3+138+9     T 150  ☒ 146 
Q 7+767+27    T 801  ☒ 803 
Q 9+477+3     T 489  ☒ 483 
Q 4+4+104     T 112  ☒ 113 
Q 19+100+9    T 128  ☒ 131 
Q 455+7+9     T 471  ☒ 473 
Q 1+9+740     T 750  ☒ 751 
Q 81+722+52   T 855  ☒ 850 
Q 162+0+11    T 173  ☒ 177 
Q 3+30+7      T 40   ☒ 39  
Q 55+6+89     T 150  ☒ 148 
Q 29+96+368   T 493  ☒ 491 
Q 51+860+5    T 916  ☒ 928 
Q 81+75+39    T 195  ☒ 199 
Q 601+55+7    T 663  ☒ 667 
Q 0+40+61     T 101  ☒ 190 
Q 270+597+6   T 873  ☒ 888 
Q 87+82+250   T 419  ☒ 403 
Q 22+566+628  T 1216 ☒ 1119
Q 436+70+726  T 1232 ☒ 1249
Q 2+72+4      T 78   ☑ 78  
Q 5+96+81     T 182  ☒ 183 
Q 17+4+254    T 275  ☒ 276 
Q 8+450+96    T 554  ☒ 552 
Q 3+5+58      T 66  

Q 5+927+6     T 938  ☒ 937 
Q 383+881+778 T 2042 ☒ 2312
Q 62+443+94   T 599  ☒ 596 
Q 433+828+4   T 1265 ☒ 1267
Q 23+70+37    T 130  ☒ 120 
Q 45+62+6     T 113  ☑ 113 
Q 66+639+7    T 712  ☒ 713 
Q 8+115+28    T 151  ☒ 152 
Q 508+57+807  T 1372 ☒ 1471
Q 39+0+60     T 99   ☒ 101 
Q 2+95+363    T 460  ☒ 463 
Q 779+54+7    T 840  ☒ 833 
Q 998+6+268   T 1272 ☒ 1379
Q 248+852+16  T 1116 ☒ 1198
Q 2+3+501     T 506  ☑ 506 
Q 513+626+894 T 2033 ☒ 2000
Q 0+26+26     T 52   ☑ 52  
Q 464+60+6    T 530  ☒ 537 
Q 10+1+928    T 939  ☒ 935 
Q 3+127+54    T 184  ☒ 190 
Q 851+5+523   T 1379 ☒ 1371
Q 52+1+27     T 80   ☒ 81  
Q 8+91+753    T 852  ☑ 852 
Q 195+24+223  T 442  ☒ 460 
Q 63+14+11    T 88   ☒ 89  
Q 8+54+2      T 64   ☑ 64  
Q 78+89+10    T 177  ☒ 181 
Q 52+69+4     T 125  ☑ 125 
Q 7+327+46    T 380  ☒ 383 
Q 184+5+496   T 685  ☒ 688 
Q 5+878+5     T 888  ☒ 882 
Q 1+976+832   T 1809 ☒ 1728
Q 7+8+45      T 60   ☒ 58  
Q 63+917+79   T 1059 ☒ 1064
Q 810+16+69   T 895  ☒ 882 
Q 6+763+575   T 1344

Q 27+69+3     T 99   ☒ 97  
Q 741+14+7    T 762  ☒ 760 
Q 944+312+351 T 1607 ☒ 1707
Q 18+16+3     T 37   ☒ 39  
Q 982+60+29   T 1071 ☒ 1040
Q 7+58+60     T 125  ☒ 124 
Q 508+282+31  T 821  ☒ 811 
Q 623+306+41  T 970  ☒ 192 
Q 7+275+468   T 750  ☒ 752 
Q 249+6+763   T 1018 ☒ 1027
Q 2+5+2       T 9    ☒ 1   
Q 19+6+93     T 118  ☒ 119 
Q 621+569+5   T 1195 ☒ 1198
Q 86+476+344  T 906  ☒ 815 
Q 19+2+63     T 84   ☒ 85  
Q 891+4+46    T 941  ☒ 944 
Q 12+6+887    T 905  ☒ 902 
Q 1+87+9      T 97   ☑ 97  
Q 800+14+68   T 882  ☒ 822 
Q 4+1+725     T 730  ☒ 724 
Q 34+339+629  T 1002 ☒ 995 
Q 78+746+15   T 839  ☒ 844 
Q 6+468+2     T 476  ☒ 472 
Q 4+17+611    T 632  ☒ 626 
Q 4+454+89    T 547  ☒ 544 
Q 9+43+30     T 82   ☒ 80  
Q 57+0+89     T 146  ☑ 146 
Q 7+633+60    T 700  ☒ 604 
Q 633+9+210   T 852  ☒ 858 
Q 666+95+4    T 765  ☑ 765 
Q 414+5+9     T 428  ☒ 422 
Q 43+9+7      T 59   ☒ 51  
Q 2+954+60    T 1016 ☒ 1010
Q 41+4+638    T 683  ☒ 785 
Q 21+7+6      T 34   ☑ 34  
Q 23+5+12     T 40  

...

Q 4+996+32    T 1032 ☒ 1037
Q 848+89+76   T 1013 ☒ 1011
Q 514+70+973  T 1557 ☒ 1455
Q 42+46+9     T 97   ☒ 99  
Q 6+773+6     T 785  ☒ 781 
Q 77+21+1     T 99   ☒ 100 
Q 816+771+30  T 1617 ☒ 1604
Q 369+0+622   T 991  ☑ 991 
Q 1+799+235   T 1035 ☒ 1044
Q 786+568+2   T 1356 ☒ 1366
Q 0+4+487     T 491  ☒ 497 
Q 923+8+6     T 937  ☒ 936 
Q 98+44+54    T 196  ☒ 192 
Q 239+9+58    T 306  ☒ 304 
Q 7+52+19     T 78   ☒ 77  
Q 235+1+92    T 328  ☒ 334 
Q 35+4+281    T 320  ☒ 318 
Q 4+5+883     T 892  ☑ 892 
Q 699+6+0     T 705  ☒ 711 
Q 909+41+5    T 955  ☒ 959 
Q 36+83+3     T 122  ☒ 121 
Q 30+81+6     T 117  ☒ 116 
Q 645+761+76  T 1482 ☒ 1452
Q 6+94+71     T 171  ☒ 172 
Q 206+542+0   T 748  ☒ 762 
Q 3+46+71     T 120  ☒ 121 
Q 585+935+2   T 1522 ☒ 1520
Q 4+78+3      T 85   ☒ 86  
Q 795+692+468 T 1955 ☒ 1822
Q 451+1+1     T 453  ☒ 454 
Q 50+706+64   T 820  ☒ 821 
Q 766+590+0   T 1356 ☒ 1353
Q 8+624+42    T 674  ☒ 675 
Q 8+575+4     T 587  ☒ 582 
Q 840+0+6     T 846  ☒ 853 
Q 648+4+9     T 661 

Q 22+38+78    T 138  ☑ 138 
Q 872+92+5    T 969  ☒ 973 
Q 69+9+66     T 144  ☒ 141 
Q 7+15+25     T 47   ☑ 47  
Q 8+23+8      T 39   ☑ 39  
Q 270+0+49    T 319  ☒ 207 
Q 362+961+31  T 1354 ☒ 1359
Q 9+29+50     T 88   ☒ 86  
Q 789+0+905   T 1694 ☒ 1719
Q 22+106+87   T 215  ☒ 211 
Q 8+73+59     T 140  ☒ 139 
Q 8+73+866    T 947  ☒ 956 
Q 69+79+9     T 157  ☒ 155 
Q 15+83+11    T 109  ☒ 110 
Q 725+887+2   T 1614 ☑ 1614
Q 57+230+7    T 294  ☒ 290 
Q 900+865+6   T 1771 ☒ 1794
Q 94+8+988    T 1090 ☒ 1084
Q 4+9+402     T 415  ☒ 417 
Q 5+71+41     T 117  ☒ 110 
Q 84+2+0      T 86   ☒ 85  
Q 20+6+48     T 74   ☒ 75  
Q 7+62+9      T 78   ☒ 77  
Q 4+2+43      T 49   ☑ 49  
Q 367+2+61    T 430  ☒ 427 
Q 12+99+385   T 496  ☒ 506 
Q 867+75+67   T 1009 ☒ 1007
Q 8+261+1     T 270  ☒ 272 
Q 8+1+446     T 455  ☒ 453 
Q 5+2+616     T 623  ☒ 620 
Q 59+274+6    T 339  ☒ 333 
Q 3+211+0     T 214  ☒ 212 
Q 79+4+891    T 974  ☒ 985 
Q 69+371+5    T 445  ☒ 447 
Q 73+4+51     T 128  ☒ 126 
Q 772+66+6    T 844 

Q 545+838+79  T 1462 ☒ 1455
Q 9+6+878     T 893  ☒ 899 
Q 5+27+697    T 729  ☒ 734 
Q 2+432+327   T 761  ☒ 755 
Q 1+15+875    T 891  ☒ 888 
Q 68+59+3     T 130  ☒ 120 
Q 50+747+43   T 840  ☒ 829 
Q 0+92+78     T 170  ☒ 176 
Q 699+354+16  T 1069 ☒ 1052
Q 37+4+919    T 960  ☒ 955 
Q 0+34+8      T 42   ☒ 41  
Q 9+28+154    T 191  ☒ 196 
Q 1+697+31    T 729  ☒ 733 
Q 979+192+15  T 1186 ☒ 1197
Q 78+730+5    T 813  ☑ 813 
Q 502+35+41   T 578  ☒ 582 
Q 38+6+162    T 206  ☒ 200 
Q 148+22+128  T 298  ☒ 303 
Q 75+194+57   T 326  ☒ 331 
Q 76+97+72    T 245  ☑ 245 
Q 63+231+712  T 1006 ☒ 905 
Q 9+1+107     T 117  ☒ 116 
Q 22+1+11     T 34   ☒ 32  
Q 11+9+53     T 73   ☒ 72  
Q 57+476+494  T 1027 ☒ 1100
Q 21+12+2     T 35   ☑ 35  
Q 24+4+98     T 126  ☒ 127 
Q 932+6+674   T 1612 ☒ 1615
Q 75+457+7    T 539  ☒ 537 
Q 41+104+924  T 1069 ☒ 1057
Q 407+24+63   T 494  ☒ 404 
Q 231+8+9     T 248  ☒ 250 
Q 1+9+347     T 357  ☒ 369 
Q 748+298+9   T 1055 ☒ 1047
Q 75+3+84     T 162  ☒ 167 
Q 86+43+18    T 147 

Q 235+24+760  T 1019 ☒ 1107
Q 61+44+70    T 175  ☒ 177 
Q 599+38+0    T 637  ☒ 647 
Q 25+961+4    T 990  ☒ 998 
Q 737+9+0     T 746  ☒ 739 
Q 1+21+50     T 72   ☒ 71  
Q 79+0+59     T 138  ☒ 137 
Q 700+44+813  T 1557 ☒ 1579
Q 54+60+3     T 117  ☒ 118 
Q 16+375+50   T 441  ☒ 440 
Q 4+6+55      T 65   ☒ 64  
Q 55+622+67   T 744  ☒ 740 
Q 699+29+7    T 735  ☒ 722 
Q 4+809+602   T 1415 ☒ 1430
Q 247+48+46   T 341  ☒ 330 
Q 5+55+981    T 1041 ☒ 1045
Q 8+92+93     T 193  ☒ 192 
Q 298+3+35    T 336  ☒ 337 
Q 65+5+37     T 107  ☑ 107 
Q 50+61+40    T 151  ☒ 148 
Q 35+4+90     T 129  ☒ 125 
Q 272+192+62  T 526  ☒ 588 
Q 61+395+1    T 457  ☒ 454 
Q 839+316+3   T 1158 ☒ 1159
Q 570+534+7   T 1111 ☒ 1117
Q 474+74+7    T 555  ☒ 554 
Q 0+583+123   T 706  ☒ 701 
Q 57+685+82   T 824  ☒ 822 
Q 1+9+866     T 876  ☑ 876 
Q 39+8+775    T 822  ☒ 824 
Q 50+9+96     T 155  ☒ 154 
Q 229+994+45  T 1268 ☒ 1269
Q 963+0+3     T 966  ☑ 966 
Q 1+221+429   T 651  ☒ 653 
Q 289+3+5     T 297  ☑ 297 
Q 476+243+23  T 742 

Q 21+87+6     T 114  ☒ 116 
Q 8+512+198   T 718  ☒ 720 
Q 6+6+435     T 447  ☒ 449 
Q 87+287+54   T 428  ☒ 409 
Q 926+3+609   T 1538 ☒ 1430
Q 667+543+164 T 1374 ☒ 1448
Q 27+9+712    T 748  ☒ 749 
Q 79+790+60   T 929  ☒ 837 
Q 635+829+839 T 2303 ☒ 2147
Q 7+6+37      T 50   ☑ 50  
Q 23+7+28     T 58   ☒ 57  
Q 81+1+50     T 132  ☒ 136 
Q 461+46+86   T 593  ☒ 596 
Q 6+116+74    T 196  ☒ 192 
Q 9+96+84     T 189  ☒ 186 
Q 9+603+29    T 641  ☒ 647 
Q 798+4+37    T 839  ☒ 840 
Q 392+6+92    T 490  ☒ 493 
Q 693+957+0   T 1650 ☒ 1644
Q 832+7+790   T 1629 ☒ 1612
Q 957+63+68   T 1088 ☒ 1194
Q 73+8+472    T 553  ☒ 554 
Q 64+98+673   T 835  ☒ 830 
Q 662+29+786  T 1477 ☒ 1483
Q 5+53+48     T 106  ☒ 108 
Q 91+3+5      T 99   ☑ 99  
Q 46+567+662  T 1275 ☒ 1283
Q 712+676+476 T 1864 ☒ 1924
Q 47+537+66   T 650  ☒ 654 
Q 7+234+17    T 258  ☒ 262 
Q 40+751+98   T 889  ☑ 889 
Q 246+779+42  T 1067 ☒ 1041
Q 1+29+761    T 791  ☒ 704 
Q 1+429+929   T 1359 ☒ 1364
Q 90+14+625   T 729  ☒ 712 
Q 149+4+5     T 158 